# General instructions

The goal of the project is to materialize a set of **exploratory workloads** over a real-world, large-scale,  open-domain KG: [WikiData](https://www.wikidata.org/wiki/Wikidata:Main_Page)

An exploratory workload  is composed by a set of queries, where each query is related to the information obtained previously.

An exploratory workload starts with a usually vague, open ended question, and does not assume the person issuing the workload has a clear understanding of the data contained in the target database or its structure.

Remeber that:

1. All the queries must run in the python notebook
2. You can use classes and properties only if you find them via a SPARQL query that must be present in the notebook
3. You do not delete useless queries. Keep everything that is synthatically valid 

```
?p <http://schema.org/name> ?name .
```
    
    is the BGP returning a human-readable name of a property or a class in Wikidata.
    
    

In [1]:
## SETUP used later

from SPARQLWrapper import SPARQLWrapper, JSON


prefixString = """
##-02e02a61c4-##
PREFIX wd: <http://www.wikidata.org/entity/> 
PREFIX wdt: <http://www.wikidata.org/prop/direct/> 
PREFIX sc: <http://schema.org/>
"""

# select and construct queries
def run_query(queryString):
    to_run = prefixString + "\n" + queryString

    sparql = SPARQLWrapper("http://a256-gc1-02.srv.aau.dk:5820/sparql")
    sparql.setTimeout(300)
    sparql.setReturnFormat(JSON)
    sparql.setQuery(to_run)

    try :
       results = sparql.query()
       json_results = results.convert()
       if len(json_results['results']['bindings'])==0:
          print("Empty")
          return 0
    
       for bindings in json_results['results']['bindings']:
          print( [ (var, value['value'])  for var, value in bindings.items() ] )

       return len(json_results['results']['bindings'])

    except Exception as e :
        print("The operation failed", e)
    
# ASk queries
def run_ask_query(queryString):
    to_run = prefixString + "\n" + queryString

    sparql = SPARQLWrapper("http://a256-gc1-02.srv.aau.dk:5820/sparql")
    sparql.setTimeout(300)
    sparql.setReturnFormat(JSON)
    sparql.setQuery(to_run)

    try :
        return sparql.query().convert()

    except Exception as e :
        print("The operation failed", e)

# Book Workflow Series ("Nobel laureates explorative search") 


Consider the following exploratory scenario:

>  Investigate the authors who won the Nobel award for literature and get information about the nationality of the winners and analyse their literary production



## Useful URIs for the current workflow
The following are given:

| IRI           | Description   | Role      |
| -----------   | -----------   |-----------|
| `wdt:P1647`   | subproperty   | predicate |
| `wdt:P31`     | instance of   | predicate |
| `wdt:P106`    | profession    | predicate | 
| `wdt:P279`    | subclass      | predicate |
| `wdt:P17`     | country       | predicate |
| `wdt:P27`     | citizenship   | predicate |
| `wd:Q37922`   | Nobel Prize in Literature     | node |
| `wd:Q36180`   | writer        | node |
| `wd:Q38`      | Italy         | node |
| `wd:Q3624078` | Sovereign state  | node |
| `wd:Q213678`  | Vatican Library  | node |


Also consider

```
?p wdt:P27 wd:Q38  . 
?p wdt:P106/wdt:P279* wd:Q36180  . 
```

is the BGP to retrieve all **italian authors**

The workload should


1. Identify the BGP for obtaining the nobel laureates and the nominees with their relevant attributes

2. Get the number of Italian, French and Iranian winners and check which nation won more awards in the last twenty years.

3. Determine how many Literature nobel laureates have the following contries: Italy, Germany, France, Romania, Denmark, Iran, and China
nobel laureates
4. How many Literature Nobel award winners have a PhD (aka Doctorate of Philosophy) (you may check if they have a doctoral advisor)?

5. Are there books from Litarature Nobel Award winners which are not present in the Vatican Library? (if so, who is the author with more books not in the Vatical Library)?

In [2]:
# start your workflow here
#
#
# IMPORTANT NOTICE:
# For several reasons, I have decided to restart this HW from the beginning after a first try. 
# The new part of the exploratory workload starts from cell 40
#

In [2]:
queryString = """
SELECT COUNT( ?p)
WHERE { 
?p wdt:P27 wd:Q38  . 
?p wdt:P106/wdt:P279* wd:Q36180  . 

} 
"""

print("Results")
run_query(queryString)

Results
[('callret-0', '46967')]


1

In [3]:
# OLD
# get all authors with their information about profession and citizenship

queryString = """
SELECT ?p ?pname ?country ?countryname ?prof ?profname
WHERE { 
?p wdt:P27 ?country  . 
?p wdt:P106 ?prof .

?country <http://schema.org/name> ?countryname .
?prof <http://schema.org/name> ?profname .
?p <http://schema.org/name> ?pname .

} 
LIMIT 20
"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/entity/Q20973626'), ('pname', 'Tondberct'), ('country', 'http://www.wikidata.org/entity/Q3122746'), ('countryname', 'Gyrwas'), ('prof', 'http://www.wikidata.org/entity/Q729924'), ('profname', 'Prince regent')]
[('p', 'http://www.wikidata.org/entity/Q16062407'), ('pname', 'Tung Ngo'), ('country', 'http://www.wikidata.org/entity/Q180573'), ('countryname', 'South Vietnam'), ('prof', 'http://www.wikidata.org/entity/Q8125919'), ('profname', 'political adviser')]
[('p', 'http://www.wikidata.org/entity/Q90365916'), ('pname', 'James Washington Lonoikauoalii McGuire'), ('country', 'http://www.wikidata.org/entity/Q156418'), ('countryname', 'Kingdom of Hawaiʻi'), ('prof', 'http://www.wikidata.org/entity/Q1511216'), ('profname', 'courtier')]
[('p', 'http://www.wikidata.org/entity/Q64712561'), ('pname', 'Jean-Pierre Huttert'), ('country', 'http://www.wikidata.org/entity/Q2719360'), ('countryname', 'Duchy of Luxembourg'), ('prof', 'http://www.wikidata.org/enti

20

In [4]:
# OLD
# get professions and their subproperties

queryString = """
SELECT DISTINCT ?prof ?profname (GROUP_CONCAT(DISTINCT ?profprop; separator=" | ") as ?props) 
(GROUP_CONCAT(DISTINCT ?proplabel; separator=" | ") as ?proplabels)
WHERE { 

?p wdt:P106/wdt:P279* ?prof .
?prof wdt:P1647 ?profprop .

?prof <http://schema.org/name> ?profname .
?profprop <http://schema.org/name> ?proplabel .

} 
GROUP BY ?prof ?profname
"""

print("Results")
run_query(queryString)

Results
Empty


0

In [5]:
# OLD
# get authors and their properties

queryString = """
SELECT DISTINCT ?props ?propslabel
WHERE { 

?p wdt:P106/wdt:P279* ?prof .
?p wdt:P1647 ?props .

?props <http://schema.org/name> ?propslabel .
} 

"""

print("Results")
run_query(queryString)

Results
Empty


0

In [7]:
# OLD
# get  from  from author node

queryString = """
SELECT DISTINCT ?p ?plabel
WHERE { 

?a wdt:P106 ?prof .
?a ?p ?o .

?p <http://schema.org/name> ?plabel .
} 
LIMIT 50

"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P6123'), ('plabel', 'B3Kat dataset ID')]
[('p', 'http://www.wikidata.org/prop/direct/P3431'), ('plabel', 'Publons publication ID')]
[('p', 'http://www.wikidata.org/prop/direct/P3903'), ('plabel', 'column')]
[('p', 'http://www.wikidata.org/prop/direct/P7104'), ('plabel', 'end of covered period')]
[('p', 'http://www.wikidata.org/prop/direct/P9271'), ('plabel', 'Kickstarter username')]
[('p', 'http://www.wikidata.org/prop/direct/P4449'), ('plabel', 'Shirat Nashim person ID')]
[('p', 'http://www.wikidata.org/prop/direct/P4836'), ('plabel', "Irish Rugby Football Union women's player ID")]
[('p', 'http://www.wikidata.org/prop/direct/P932'), ('plabel', 'PMCID')]
[('p', 'http://www.wikidata.org/prop/direct/P8830'), ('plabel', 'Swiss-Gym Female ID')]
[('p', 'http://www.wikidata.org/prop/direct/P3332'), ('plabel', 'ACM Digital Library citation ID')]
[('p', 'http://www.wikidata.org/prop/direct/P6480'), ('plabel', 'IEEE Xplore document ID')]
[('p

50

In [6]:
# OLD
# get subjects and objects which are related by "country" predicate

queryString = """
SELECT ?a ?alabel ?o ?olabel  
WHERE { 

?a wdt:P17 ?o .

?a <http://schema.org/name> ?alabel .
?o <http://schema.org/name> ?olabel .
} 
LIMIT 50

"""

print("Results")
run_query(queryString)

Results
[('a', 'http://www.wikidata.org/entity/Q2535173'), ('alabel', 'South Vietnam Air Force'), ('o', 'http://www.wikidata.org/entity/Q180573'), ('olabel', 'South Vietnam')]
[('a', 'http://www.wikidata.org/entity/Q18603767'), ('alabel', 'religion in Greenland'), ('o', 'http://www.wikidata.org/entity/Q223'), ('olabel', 'Greenland')]
[('a', 'http://www.wikidata.org/entity/Q307881'), ('alabel', 'Freedom and Reform Party'), ('o', 'http://www.wikidata.org/entity/Q23681'), ('olabel', 'Turkish Republic of Northern Cyprus')]
[('a', 'http://www.wikidata.org/entity/Q1415784'), ('alabel', 'Military of Northern Cyprus'), ('o', 'http://www.wikidata.org/entity/Q23681'), ('olabel', 'Turkish Republic of Northern Cyprus')]
[('a', 'http://www.wikidata.org/entity/Q17070503'), ('alabel', 'flora of the Dominican Republic'), ('o', 'http://www.wikidata.org/entity/Q786'), ('olabel', 'Dominican Republic')]
[('a', 'http://www.wikidata.org/entity/Q5290779'), ('alabel', 'Dominican Republic at the Pan American G

50

In [9]:
# OLD
# get superclass over the node "Nobel Prize in Literature"

queryString = """
SELECT ?p ?plabel  
WHERE { 

?p wdt:P279 wd:Q37922 .

?p <http://schema.org/name> ?plabel .
} 
LIMIT 50

"""

print("Results")
run_query(queryString)

Results
Empty


0

In [10]:
# OLD
# get node which has "Nobel Prize in Literature" as instance

queryString = """
SELECT ?a ?alabel 
WHERE { 

wd:Q37922 wdt:P31 ?a .

?a <http://schema.org/name> ?alabel .
} 
LIMIT 50

"""

print("Results")
run_query(queryString)

Results
[('a', 'http://www.wikidata.org/entity/Q378427'), ('alabel', 'literary award')]


1

In [11]:
# OLD
# get instances of "Literary award"

queryString = """
SELECT ?inst ?instlabel
WHERE { 

?inst wdt:P31 wd:Q378427 .

?inst <http://schema.org/name> ?instlabel .

} 
LIMIT 20

"""

print("Results")
run_query(queryString)

Results
[('inst', 'http://www.wikidata.org/entity/Q5475056'), ('instlabel', 'Anagrama Essay Prize')]
[('inst', 'http://www.wikidata.org/entity/Q108172262'), ('instlabel', 'Sahitya Akademi Award in Bengali')]
[('inst', 'http://www.wikidata.org/entity/Q6948884'), ('instlabel', 'Mystery Writers of Japan Award')]
[('inst', 'http://www.wikidata.org/entity/Q897940'), ('instlabel', 'Brandenburgischer Literaturpreis')]
[('inst', 'http://www.wikidata.org/entity/Q15977880'), ('instlabel', 'Scaglione Prize for Studies in Germanic Languages and Literatures')]
[('inst', 'http://www.wikidata.org/entity/Q60492234'), ('instlabel', 'Odisha Sahitya Akademi Ovation')]
[('inst', 'http://www.wikidata.org/entity/Q15842634'), ('instlabel', 'Roald Dahl Funny Prize')]
[('inst', 'http://www.wikidata.org/entity/Q23068423'), ('instlabel', "grand prix de l'héroïne Madame Figaro du roman étranger")]
[('inst', 'http://www.wikidata.org/entity/Q487497'), ('instlabel', 'Manhae Prize')]
[('inst', 'http://www.wikidata.or

20

In [12]:
# OLD
# get predicate from "Nobel Prize in Literature"

queryString = """
SELECT ?p ?plabel
WHERE { 

wd:Q37922 ?p ?o .

?p <http://schema.org/name> ?plabel .

} 
LIMIT 50

"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P1296'), ('plabel', 'Gran Enciclopèdia Catalana ID')]
[('p', 'http://www.wikidata.org/prop/direct/P1346'), ('plabel', 'winner')]
[('p', 'http://www.wikidata.org/prop/direct/P1346'), ('plabel', 'winner')]
[('p', 'http://www.wikidata.org/prop/direct/P1346'), ('plabel', 'winner')]
[('p', 'http://www.wikidata.org/prop/direct/P1346'), ('plabel', 'winner')]
[('p', 'http://www.wikidata.org/prop/direct/P1346'), ('plabel', 'winner')]
[('p', 'http://www.wikidata.org/prop/direct/P1346'), ('plabel', 'winner')]
[('p', 'http://www.wikidata.org/prop/direct/P1346'), ('plabel', 'winner')]
[('p', 'http://www.wikidata.org/prop/direct/P1346'), ('plabel', 'winner')]
[('p', 'http://www.wikidata.org/prop/direct/P1346'), ('plabel', 'winner')]
[('p', 'http://www.wikidata.org/prop/direct/P1346'), ('plabel', 'winner')]
[('p', 'http://www.wikidata.org/prop/direct/P1346'), ('plabel', 'winner')]
[('p', 'http://www.wikidata.org/prop/direct/P1346'), ('plabel', 'winn

47

In [13]:
# OLD
# get subjects and predicates linked to "Literary award"

queryString = """
SELECT ?sc ?sclabel ?p ?plabel
WHERE { 

?sc ?p wd:Q378427 .

?sc <http://schema.org/name> ?sclabel .
?p <http://schema.org/name> ?plabel .

} 
LIMIT 50

"""

print("Results")
run_query(queryString)

Results
[('sc', 'http://www.wikidata.org/entity/Q30324712'), ('sclabel', 'Grand Prix of Literary Associations'), ('p', 'http://www.wikidata.org/prop/direct/P136'), ('plabel', 'genre')]
[('sc', 'http://www.wikidata.org/entity/Q106406561'), ('sclabel', 'Paloma Chen'), ('p', 'http://www.wikidata.org/prop/direct/P166'), ('plabel', 'award received')]
[('sc', 'http://www.wikidata.org/entity/Q452860'), ('sclabel', 'Amma Darko'), ('p', 'http://www.wikidata.org/prop/direct/P166'), ('plabel', 'award received')]
[('sc', 'http://www.wikidata.org/entity/Q97769499'), ('sclabel', "Maya Barne'a Goldberg"), ('p', 'http://www.wikidata.org/prop/direct/P166'), ('plabel', 'award received')]
[('sc', 'http://www.wikidata.org/entity/Q106328756'), ('sclabel', 'Gabriele Pulli'), ('p', 'http://www.wikidata.org/prop/direct/P166'), ('plabel', 'award received')]
[('sc', 'http://www.wikidata.org/entity/Q97924350'), ('sclabel', 'Dafna Ben-Zvi'), ('p', 'http://www.wikidata.org/prop/direct/P166'), ('plabel', 'award rec

50

In [14]:
# OLD
# get predicates of a person, using "Paloma Chen" instance

queryString = """
SELECT ?p ?plabel ?o ?olabel
WHERE { 

wd:Q106406561 ?p ?o .

?p <http://schema.org/name> ?plabel .
?o <http://schema.org/name> ?olabel .

} 
LIMIT 50

"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P19'), ('plabel', 'place of birth'), ('o', 'http://www.wikidata.org/entity/Q11959'), ('olabel', 'Alicante')]
[('p', 'http://www.wikidata.org/prop/direct/P27'), ('plabel', 'country of citizenship'), ('o', 'http://www.wikidata.org/entity/Q148'), ('olabel', "People's Republic of China")]
[('p', 'http://www.wikidata.org/prop/direct/P106'), ('plabel', 'occupation'), ('o', 'http://www.wikidata.org/entity/Q1930187'), ('olabel', 'journalist')]
[('p', 'http://www.wikidata.org/prop/direct/P27'), ('plabel', 'country of citizenship'), ('o', 'http://www.wikidata.org/entity/Q29'), ('olabel', 'Spain')]
[('p', 'http://www.wikidata.org/prop/direct/P166'), ('plabel', 'award received'), ('o', 'http://www.wikidata.org/entity/Q378427'), ('olabel', 'literary award')]
[('p', 'http://www.wikidata.org/prop/direct/P106'), ('plabel', 'occupation'), ('o', 'http://www.wikidata.org/entity/Q49757'), ('olabel', 'poet')]
[('p', 'http://www.wikidata.org/prop/direct/P3

12

In [15]:
# OLD
# get predicates from "educated at" predicate

queryString = """
SELECT DISTINCT ?p ?plabel
WHERE { 

wd:P69 ?p ?o .

?p <http://schema.org/name> ?plabel .

} 

"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P1628'), ('plabel', 'equivalent property')]
[('p', 'http://www.wikidata.org/prop/direct/P2236'), ('plabel', 'external subproperty')]
[('p', 'http://www.wikidata.org/prop/direct/P31'), ('plabel', 'instance of')]
[('p', 'http://www.wikidata.org/prop/direct/P1659'), ('plabel', 'see also')]
[('p', 'http://www.wikidata.org/prop/direct/P1629'), ('plabel', 'Wikidata item of this property')]
[('p', 'http://www.wikidata.org/prop/direct/P1855'), ('plabel', 'Wikidata property example')]
[('p', 'http://www.wikidata.org/prop/direct/P2302'), ('plabel', 'property constraint')]
[('p', 'http://www.wikidata.org/prop/direct/P2875'), ('plabel', 'property usage tracking category')]
[('p', 'http://www.wikidata.org/prop/direct/P3254'), ('plabel', 'property proposal discussion')]
[('p', 'http://www.wikidata.org/prop/direct/P3734'), ('plabel', 'category for value same as Wikidata')]
[('p', 'http://www.wikidata.org/prop/direct/P7087'), ('plabel', 'inverse labe

12

In [16]:
# OLD
# get object from following path "person"->"educated at"->"equivalent property"

queryString = """
SELECT DISTINCT ?o ?olabel
WHERE { 

wd:P69 wd:1628 ?o .

?o <http://schema.org/name> ?olabel .

} 

"""

print("Results")
run_query(queryString)

Results
Empty


0

In [17]:
# OLD
# get class of "Paloma Chen"

queryString = """
SELECT DISTINCT ?o ?olabel
WHERE { 

wd:Q106406561 wdt:P31 ?o .

?o <http://schema.org/name> ?olabel .

} 

"""

print("Results")
run_query(queryString)

Results
[('o', 'http://www.wikidata.org/entity/Q5'), ('olabel', 'human')]


1

In [18]:
# OLD
# get predicates from "human" entity

queryString = """
SELECT DISTINCT ?p ?plabel
WHERE { 

wd:Q106406561 wdt:P31 ?o .
?o ?p ?o2 .

?p <http://schema.org/name> ?plabel .

} 

"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P5806'), ('plabel', 'SNOMED CT identifier')]
[('p', 'http://www.wikidata.org/prop/direct/P1036'), ('plabel', 'Dewey Decimal Classification')]
[('p', 'http://www.wikidata.org/prop/direct/P1051'), ('plabel', 'PSH ID')]
[('p', 'http://www.wikidata.org/prop/direct/P1056'), ('plabel', 'product or material produced')]
[('p', 'http://www.wikidata.org/prop/direct/P1225'), ('plabel', 'U.S. National Archives Identifier')]
[('p', 'http://www.wikidata.org/prop/direct/P1245'), ('plabel', 'OmegaWiki Defined Meaning')]
[('p', 'http://www.wikidata.org/prop/direct/P1256'), ('plabel', 'Iconclass notation')]
[('p', 'http://www.wikidata.org/prop/direct/P129'), ('plabel', 'physically interacts with')]
[('p', 'http://www.wikidata.org/prop/direct/P1296'), ('plabel', 'Gran Enciclopèdia Catalana ID')]
[('p', 'http://www.wikidata.org/prop/direct/P1343'), ('plabel', 'described by source')]
[('p', 'http://www.wikidata.org/prop/direct/P1417'), ('plabel', 'Encyclo

74

In [19]:
# OLD
# get objects from path "human"->"studied by"

queryString = """
SELECT ?o2 ?o2label
WHERE { 

wd:Q106406561 wdt:P31 ?o .
?o wdt:P2579 ?o2 .

?o2 <http://schema.org/name> ?o2label .

} 

"""

print("Results")
run_query(queryString)

Results
[('o2', 'http://www.wikidata.org/entity/Q23404'), ('o2label', 'anthropology')]
[('o2', 'http://www.wikidata.org/entity/Q720858'), ('o2label', 'human ecology')]


2

In [20]:
# OLD
# get predicates towards "Paloma Chen" instance

queryString = """
SELECT ?p ?plabel
WHERE { 

?s ?p wd:Q106406561 .

?p <http://schema.org/name> ?plabel .

} 
LIMIT 50

"""

print("Results")
run_query(queryString)

Results
Empty


0

In [21]:
# OLD
# get predicates which match "nominee" on label

queryString = """
SELECT ?s ?slabel ?o ?olabel
WHERE { 

?s wdt:P31 wd:Q5 .
?s ?p ?o .

?s <http://schema.org/name> ?slabel .
?o <http://schema.org/name> ?olabel .
?p <http://schema.org/name> ?plabel .

FILTER REGEX (?plabel, "nominee")

} 

"""

print("Results")
run_query(queryString)

Results
The operation failed timed out


In [22]:
# OLD
# get distinct predicates linked to "Literary award"

queryString = """
SELECT DISTINCT ?p ?plabel
WHERE { 

?s ?p wd:Q378427 .

?p <http://schema.org/name> ?plabel .

} 

"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P1269'), ('plabel', 'facet of')]
[('p', 'http://www.wikidata.org/prop/direct/P136'), ('plabel', 'genre')]
[('p', 'http://www.wikidata.org/prop/direct/P166'), ('plabel', 'award received')]
[('p', 'http://www.wikidata.org/prop/direct/P279'), ('plabel', 'subclass of')]
[('p', 'http://www.wikidata.org/prop/direct/P301'), ('plabel', "category's main topic")]
[('p', 'http://www.wikidata.org/prop/direct/P31'), ('plabel', 'instance of')]
[('p', 'http://www.wikidata.org/prop/direct/P360'), ('plabel', 'is a list of')]
[('p', 'http://www.wikidata.org/prop/direct/P4224'), ('plabel', 'category contains')]
[('p', 'http://www.wikidata.org/prop/direct/P921'), ('plabel', 'main subject')]
[('p', 'http://www.wikidata.org/prop/direct/P971'), ('plabel', 'category combines topics')]


10

In [23]:
# OLD
# get predicates to "Nobel Prize in Literature"

queryString = """
SELECT DISTINCT ?p ?plabel
WHERE { 

?s ?p wd:Q37922 .

?p <http://schema.org/name> ?plabel .

} 

"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P1411'), ('plabel', 'nominated for')]
[('p', 'http://www.wikidata.org/prop/direct/P166'), ('plabel', 'award received')]
[('p', 'http://www.wikidata.org/prop/direct/P179'), ('plabel', 'part of the series')]
[('p', 'http://www.wikidata.org/prop/direct/P301'), ('plabel', "category's main topic")]
[('p', 'http://www.wikidata.org/prop/direct/P31'), ('plabel', 'instance of')]
[('p', 'http://www.wikidata.org/prop/direct/P360'), ('plabel', 'is a list of')]
[('p', 'http://www.wikidata.org/prop/direct/P527'), ('plabel', 'has part')]
[('p', 'http://www.wikidata.org/prop/direct/P793'), ('plabel', 'significant event')]
[('p', 'http://www.wikidata.org/prop/direct/P921'), ('plabel', 'main subject')]
[('p', 'http://www.wikidata.org/prop/direct/P971'), ('plabel', 'category combines topics')]


10

In [24]:
# OLD
# get nominated people for "Nobel Prize in Literature"

queryString = """
SELECT ?s ?slabel
WHERE { 

?s wdt:P1411 wd:Q37922 .

?s <http://schema.org/name> ?slabel .

} 

LIMIT 50

"""

print("Results")
run_query(queryString)

Results
[('s', 'http://www.wikidata.org/entity/Q135640'), ('slabel', 'Valery Larbaud')]
[('s', 'http://www.wikidata.org/entity/Q2475967'), ('slabel', 'Adrien Albert Marie de Mun')]
[('s', 'http://www.wikidata.org/entity/Q216398'), ('slabel', 'Alan Sillitoe')]
[('s', 'http://www.wikidata.org/entity/Q164469'), ('slabel', 'Pierre Emmanuel')]
[('s', 'http://www.wikidata.org/entity/Q727717'), ('slabel', 'Ramón Pérez de Ayala')]
[('s', 'http://www.wikidata.org/entity/Q79055'), ('slabel', 'Franz Theodor Csokor')]
[('s', 'http://www.wikidata.org/entity/Q76332'), ('slabel', 'Rudolf Alexander Schröder')]
[('s', 'http://www.wikidata.org/entity/Q773389'), ('slabel', 'Giorgos Theotokás')]
[('s', 'http://www.wikidata.org/entity/Q159552'), ('slabel', 'Johannes V. Jensen')]
[('s', 'http://www.wikidata.org/entity/Q1371568'), ('slabel', 'Johannes Jørgensen')]
[('s', 'http://www.wikidata.org/entity/Q112588'), ('slabel', 'Franz Karl Ginzkey')]
[('s', 'http://www.wikidata.org/entity/Q34743'), ('slabel', 'R

50

In [25]:
# OLD
# get predicates from "nominated for" entity

queryString = """
SELECT DISTINCT ?p ?plabel
WHERE { 

wdt:P1411 ?p ?o .

?p <http://schema.org/name> ?plabel .

} 

"""

print("Results")
run_query(queryString)

Results
Empty


0

In [7]:
# OLD
# get nominated people and winners related to "Nobel Prize in Literature"

queryString = """
SELECT ?person ?plabel ?place ?birth ?blabel (GROUP_CONCAT(DISTINCT ?occ; separator= " | ") as ?occupation) (GROUP_CONCAT(DISTINCT ?occlabel; separator= " | ") as ?occupationlabel) ?education ?edulabel ?employer ?emplabel
WHERE { 

{
    wd:Q37922 wdt:P1346 ?person .
    ?person wdt:P31 wd:Q5 ;
            wdt:P19 ?birth ;
            wdt:P106 ?occ ;
            wdt:P69 ?education ;
            wdt:P108 ?employer .
            
    ?person <http://schema.org/name> ?plabel .
    ?birth <http://schema.org/name> ?blabel .
    ?occ <http://schema.org/name> ?occlabel .
    ?education <http://schema.org/name> ?edulabel .
    ?employer <http://schema.org/name> ?emplabel .
    
    VALUES ?place {"winner"}
}
UNION
{
    ?person wdt:P1411 wd:Q37922 ;
            wdt:P31 wd:Q5 ;
            wdt:P19 ?birth ;
            wdt:P106 ?occ ;
            wdt:P69 ?education ;
            wdt:P108 ?employer .
            
    ?person <http://schema.org/name> ?plabel .
    ?birth <http://schema.org/name> ?blabel .
    ?occ <http://schema.org/name> ?occlabel .
    ?education <http://schema.org/name> ?edulabel .
    ?employer <http://schema.org/name> ?emplabel .
    
    VALUES ?place {"nominated"}
}
} 
GROUP BY ?person ?plabel ?place ?birth ?blabel ?education ?edulabel ?employer ?emplabel

"""

print("Results")
run_query(queryString)

Results
[('person', 'http://www.wikidata.org/entity/Q380842'), ('plabel', 'Joseph Bédier'), ('place', 'nominated'), ('birth', 'http://www.wikidata.org/entity/Q245546'), ('blabel', '6th arrondissement of Paris'), ('occupation', 'http://www.wikidata.org/entity/Q121594 | http://www.wikidata.org/entity/Q13418253 | http://www.wikidata.org/entity/Q2504617 | http://www.wikidata.org/entity/Q4263842'), ('occupationlabel', 'literary critic | philologist | professor | romanist'), ('education', 'http://www.wikidata.org/entity/Q83259'), ('edulabel', 'École normale supérieure'), ('employer', 'http://www.wikidata.org/entity/Q214654'), ('emplabel', 'Sorbonne')]
[('person', 'http://www.wikidata.org/entity/Q47162'), ('plabel', 'Romain Rolland'), ('place', 'nominated'), ('birth', 'http://www.wikidata.org/entity/Q213294'), ('blabel', 'Clamecy'), ('occupation', 'http://www.wikidata.org/entity/Q11774202 | http://www.wikidata.org/entity/Q12144794 | http://www.wikidata.org/entity/Q14915627 | http://www.wikida

691

In [27]:
# OLD
# get predicates from "nominated for" predicate

queryString = """
SELECT DISTINCT ?p ?o
WHERE { 

wdt:P1411 ?p ?o .

}

"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.w3.org/1999/02/22-rdf-syntax-ns#type'), ('o', 'http://www.w3.org/2002/07/owl#ObjectProperty')]
[('p', 'http://schema.org/name'), ('o', 'nominated for')]


2

In [28]:
# OLD
# get predicate from "Nobel Prize in Literature"

queryString = """
SELECT DISTINCT ?o ?olabel
WHERE { 

wd:Q37922 wdt:P1346 ?o .

?o <http://schema.org/name> ?olabel .

} 
LIMIT 50

"""

print("Results")
run_query(queryString)

Results
[('o', 'http://www.wikidata.org/entity/Q159552'), ('olabel', 'Johannes V. Jensen')]
[('o', 'http://www.wikidata.org/entity/Q254032'), ('olabel', 'Olga Tokarczuk')]
[('o', 'http://www.wikidata.org/entity/Q7241'), ('olabel', 'Rabindranath Tagore')]
[('o', 'http://www.wikidata.org/entity/Q392'), ('olabel', 'Bob Dylan')]
[('o', 'http://www.wikidata.org/entity/Q44593'), ('olabel', 'V. S. Naipaul')]
[('o', 'http://www.wikidata.org/entity/Q121180'), ('olabel', 'Władysław Reymont')]
[('o', 'http://www.wikidata.org/entity/Q47561'), ('olabel', 'Ivo Andrić')]
[('o', 'http://www.wikidata.org/entity/Q6538'), ('olabel', 'Günter Grass')]
[('o', 'http://www.wikidata.org/entity/Q44107'), ('olabel', 'Peter Handke')]
[('o', 'http://www.wikidata.org/entity/Q72334'), ('olabel', 'Toni Morrison')]
[('o', 'http://www.wikidata.org/entity/Q225554'), ('olabel', 'Henrik Pontoppidan')]
[('o', 'http://www.wikidata.org/entity/Q272855'), ('olabel', 'Kazuo Ishiguro')]
[('o', 'http://www.wikidata.org/entity/Q47

15

In [29]:
# OLD
# get predicates from "Literary award"

queryString = """
SELECT DISTINCT ?p ?plabel ?o ?olabel
WHERE { 

wd:Q378427 ?p ?o .

?p <http://schema.org/name> ?plabel .
?o <http://schema.org/name> ?olabel .

} 

"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P279'), ('plabel', 'subclass of'), ('o', 'http://www.wikidata.org/entity/Q618779'), ('olabel', 'award')]
[('p', 'http://www.wikidata.org/prop/direct/P31'), ('plabel', 'instance of'), ('o', 'http://www.wikidata.org/entity/Q107467117'), ('olabel', 'type of award')]
[('p', 'http://www.wikidata.org/prop/direct/P279'), ('plabel', 'subclass of'), ('o', 'http://www.wikidata.org/entity/Q1656682'), ('olabel', 'event')]
[('p', 'http://www.wikidata.org/prop/direct/P910'), ('plabel', "topic's main category"), ('o', 'http://www.wikidata.org/entity/Q6519853'), ('olabel', 'Category:Literary awards')]


4

In [30]:
# OLD
# get predicates from "award"

queryString = """
SELECT DISTINCT ?p ?plabel
WHERE { 

wd:Q618779 ?p ?o .

?p <http://schema.org/name> ?plabel .

} 

"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P1014'), ('plabel', 'Art & Architecture Thesaurus ID')]
[('p', 'http://www.wikidata.org/prop/direct/P1149'), ('plabel', 'Library of Congress Classification')]
[('p', 'http://www.wikidata.org/prop/direct/P1151'), ('plabel', "topic's main Wikimedia portal")]
[('p', 'http://www.wikidata.org/prop/direct/P1225'), ('plabel', 'U.S. National Archives Identifier')]
[('p', 'http://www.wikidata.org/prop/direct/P1296'), ('plabel', 'Gran Enciclopèdia Catalana ID')]
[('p', 'http://www.wikidata.org/prop/direct/P1343'), ('plabel', 'described by source')]
[('p', 'http://www.wikidata.org/prop/direct/P1382'), ('plabel', 'partially coincident with')]
[('p', 'http://www.wikidata.org/prop/direct/P1424'), ('plabel', "topic's main template")]
[('p', 'http://www.wikidata.org/prop/direct/P1687'), ('plabel', 'Wikidata property')]
[('p', 'http://www.wikidata.org/prop/direct/P1709'), ('plabel', 'equivalent class')]
[('p', 'http://www.wikidata.org/prop/direct/P18'

53

In [31]:
# OLD
# get objects from following path "award"->"properties for this type"

queryString = """
SELECT ?o2 ?o2label
WHERE { 

wd:Q618779 ?p ?o1 .
?p wdt:P1963 ?o2 .

?o2 <http://schema.org/name> ?o2label .

} 

"""

print("Results")
run_query(queryString)

Results
Empty


0

In [32]:
# OLD
# get how many "Nobel prize for literature" Toni Morrison won (starting from "Nobel prize for literature" node)

queryString = """
SELECT COUNT(?person)
WHERE { 

    wd:Q37922 wdt:P1346 ?person .
    
    ?person <http://schema.org/name> "Toni Morrison"^^xsd:string .
} 

"""

print("Results")
run_query(queryString)

Results
[('callret-0', '0')]


1

In [33]:
# OLD
# get how many "Nobel prize for literal" Toni Morrison won (starting from "Toni Morrison" node)

queryString = """
SELECT COUNT(?person)
WHERE { 

    ?person wdt:P166/wd:Q378427 wd:Q37922 .
    
    ?person <http://schema.org/name> "Toni Morrison"^^xsd:string .
} 

"""

print("Results")
run_query(queryString)

Results
[('callret-0', '0')]


1

In [34]:
# OLD
# get properties from the following path "human"->"person"->"award received"

queryString = """
SELECT DISTINCT ?o ?olabel ?p2 ?p2label ?o2 ?o2label
WHERE { 

    ?p wdt:P166 ?o ;
        wdt:P31 wd:Q5 .
    ?o ?p2 ?o2 .
    
    ?o <http://schema.org/name> ?olabel .
    ?p2 <http://schema.org/name> ?p2label .
    ?o2 <http://schema.org/name> ?o2label .
} 

"""

print("Results")
run_query(queryString)

Results
[('o', 'http://www.wikidata.org/entity/Q14900498'), ('olabel', 'Officer of the Order of Leopold'), ('p2', 'http://www.wikidata.org/prop/direct/P3729'), ('p2label', 'next lower rank'), ('o2', 'http://www.wikidata.org/entity/Q14900497'), ('o2label', 'Knight of the Order of Leopold')]
[('o', 'http://www.wikidata.org/entity/Q28870394'), ('olabel', 'Grand Cross of the Order of St. Raymond of Peñafort'), ('p2', 'http://www.wikidata.org/prop/direct/P3729'), ('p2label', 'next lower rank'), ('o2', 'http://www.wikidata.org/entity/Q32579103'), ('o2label', 'Cross of Honour of the Order of St. Raymond of Peñafort')]
[('o', 'http://www.wikidata.org/entity/Q15715257'), ('olabel', 'Grand Cross of the Order of Polonia Restituta'), ('p2', 'http://www.wikidata.org/prop/direct/P3729'), ('p2label', 'next lower rank'), ('o2', 'http://www.wikidata.org/entity/Q15715254'), ('o2label', 'Commander with Star of the Order of Polonia Restituta')]
[('o', 'http://www.wikidata.org/entity/Q21954284'), ('olabel'

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



[('o', 'http://www.wikidata.org/entity/Q94121'), ('olabel', 'Grand Order of King Tomislav'), ('p2', 'http://www.wikidata.org/prop/direct/P3729'), ('p2label', 'next lower rank'), ('o2', 'http://www.wikidata.org/entity/Q94499'), ('o2label', 'Grand Order of Queen Jelena')]
[('o', 'http://www.wikidata.org/entity/Q1441539'), ('olabel', 'American Music Award for Favorite Country Album'), ('p2', 'http://www.wikidata.org/prop/direct/P1346'), ('p2label', 'winner'), ('o2', 'http://www.wikidata.org/entity/Q215546'), ('o2label', 'Carrie Underwood')]
[('o', 'http://www.wikidata.org/entity/Q1441539'), ('olabel', 'American Music Award for Favorite Country Album'), ('p2', 'http://www.wikidata.org/prop/direct/P1346'), ('p2label', 'winner'), ('o2', 'http://www.wikidata.org/entity/Q380927'), ('o2label', 'Alan Jackson')]
[('o', 'http://www.wikidata.org/entity/Q1441539'), ('olabel', 'American Music Award for Favorite Country Album'), ('p2', 'http://www.wikidata.org/prop/direct/P1346'), ('p2label', 'winner'

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



[('o', 'http://www.wikidata.org/entity/Q3406077'), ('olabel', 'Prix Émile-Nelligan'), ('p2', 'http://www.wikidata.org/prop/direct/P138'), ('p2label', 'named after'), ('o2', 'http://www.wikidata.org/entity/Q2392492'), ('o2label', 'Émile Nelligan')]
[('o', 'http://www.wikidata.org/entity/Q19278508'), ('olabel', 'Mac Orlan Prize'), ('p2', 'http://www.wikidata.org/prop/direct/P138'), ('p2label', 'named after'), ('o2', 'http://www.wikidata.org/entity/Q546952'), ('o2label', 'Pierre Mac Orlan')]
[('o', 'http://www.wikidata.org/entity/Q20891315'), ('olabel', 'Gebran Tueni Award'), ('p2', 'http://www.wikidata.org/prop/direct/P138'), ('p2label', 'named after'), ('o2', 'http://www.wikidata.org/entity/Q527870'), ('o2label', 'Gebran Tueni')]
[('o', 'http://www.wikidata.org/entity/Q3540433'), ('olabel', 'Lionel Conacher Award'), ('p2', 'http://www.wikidata.org/prop/direct/P138'), ('p2label', 'named after'), ('o2', 'http://www.wikidata.org/entity/Q934093'), ('o2label', 'Lionel Conacher')]
[('o', 'htt

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



[('o', 'http://www.wikidata.org/entity/Q34095'), ('olabel', 'bronze'), ('p2', 'http://www.wikidata.org/prop/direct/P1343'), ('p2label', 'described by source'), ('o2', 'http://www.wikidata.org/entity/Q602358'), ('o2label', 'Brockhaus and Efron Encyclopedic Dictionary')]
[('o', 'http://www.wikidata.org/entity/Q34095'), ('olabel', 'bronze'), ('p2', 'http://www.wikidata.org/prop/direct/P1889'), ('p2label', 'different from'), ('o2', 'http://www.wikidata.org/entity/Q39782'), ('o2label', 'brass')]
[('o', 'http://www.wikidata.org/entity/Q34095'), ('olabel', 'bronze'), ('p2', 'http://www.wikidata.org/prop/direct/P279'), ('p2label', 'subclass of'), ('o2', 'http://www.wikidata.org/entity/Q518350'), ('o2label', 'copper alloy')]
[('o', 'http://www.wikidata.org/entity/Q34095'), ('olabel', 'bronze'), ('p2', 'http://www.wikidata.org/prop/direct/P279'), ('p2label', 'subclass of'), ('o2', 'http://www.wikidata.org/entity/Q21685333'), ('o2label', 'sculpture material')]
[('o', 'http://www.wikidata.org/enti

113649

In [35]:
# OLD
# get class of which "art prize" is an instance

queryString = """
SELECT DISTINCT ?o ?olabel
WHERE { 

    wd:Q1792571 wdt:P31 ?o .
    
    ?o <http://schema.org/name> ?olabel .
} 

"""

print("Results")
run_query(queryString)

Results
[('o', 'http://www.wikidata.org/entity/Q107467117'), ('olabel', 'type of award')]


1

In [36]:
# OLD
# get instance of which "Nobel Prize in Literature"

queryString = """
SELECT DISTINCT ?s ?slabel
WHERE { 

    ?s wdt:P31 wd:Q37922 .
    
    ?s <http://schema.org/name> ?slabel .
} 

"""

print("Results")
run_query(queryString)

Results
Empty


0

In [37]:
# OLD
# get lists from "haslist" property of "Nobel Prize of Literature"

queryString = """
SELECT ?o ?olabel
WHERE { 

    wd:Q37922 wdt:P2354 ?o .
    
    ?o <http://schema.org/name> ?olabel .
} 

"""

print("Results")
run_query(queryString)

Results
[('o', 'http://www.wikidata.org/entity/Q6461210'), ('olabel', 'list of Nobel laureates in Literature')]


1

In [38]:
# OLD
# get lists from "haslist" property and their objects of "Nobel Prize of Literature"

queryString = """
SELECT ?p ?plabel ?o2 ?o2label
WHERE { 

    wd:Q37922 wdt:P2354 ?o .
    ?o ?p ?o2 .
    
    ?p <http://schema.org/name> ?plabel .
    ?o2 <http://schema.org/name> ?o2label .
    
} 

"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P31'), ('plabel', 'instance of'), ('o2', 'http://www.wikidata.org/entity/Q13406463'), ('o2label', 'Wikimedia list article')]
[('p', 'http://www.wikidata.org/prop/direct/P360'), ('plabel', 'is a list of'), ('o2', 'http://www.wikidata.org/entity/Q5'), ('o2label', 'human')]
[('p', 'http://www.wikidata.org/prop/direct/P1754'), ('plabel', 'category related to list'), ('o2', 'http://www.wikidata.org/entity/Q6736049'), ('o2label', 'Category:Nobel laureates in Literature')]


3

In [39]:
# OLD
# get lists from "haslist" property and their objects of "Nobel Prize of Literature"

queryString = """
SELECT DISTINCT ?p ?plabel
WHERE { 

    ?s wdt:P31 wd:Q5 ;
        ?p ?o .
        
    FILTER(!isLiteral(?o))
    FILTER REGEX(?p, "(date)|(award)|(prize)")
    ?p <http://schema.org/name> ?plabel .
    
} 

"""

print("Results")
run_query(queryString)

Results
The operation failed timed out


In [45]:
# get predicates from "human" whose profession is "writer"

queryString = """
SELECT DISTINCT ?p ?plbl
WHERE { 

?s wdt:P106/wdt:P279* wd:Q36180  ;
    ?p ?o .
    
?p <http://schema.org/name> ?plbl .

} 
ORDER BY ?plbl
"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P8992'), ('plbl', '1914-1918-Online ID')]
[('p', 'http://www.wikidata.org/prop/direct/P5716'), ('plbl', '2006 Commonwealth Games athlete ID')]
[('p', 'http://www.wikidata.org/prop/direct/P6953'), ('plbl', '2014 Commonwealth Games athlete ID')]
[('p', 'http://www.wikidata.org/prop/direct/P7397'), ('plbl', '247Sports ID')]
[('p', 'http://www.wikidata.org/prop/direct/P3314'), ('plbl', '365chess player ID')]
[('p', 'http://www.wikidata.org/prop/direct/P4896'), ('plbl', '3D model')]
[('p', 'http://www.wikidata.org/prop/direct/P3605'), ('plbl', '90minut player ID')]
[('p', 'http://www.wikidata.org/prop/direct/P9046'), ('plbl', 'A*dS Encyclopedia ID')]
[('p', 'http://www.wikidata.org/prop/direct/P9634'), ('plbl', 'AADFI member ID')]
[('p', 'http://www.wikidata.org/prop/direct/P8783'), ('plbl', 'AAGM person or institution ID')]
[('p', 'http://www.wikidata.org/prop/direct/P5756'), ('plbl', 'ABMC person ID')]
[('p', 'http://www.wikidata.org/pro

3570

In [47]:
# get predicates to "Nobel Prize in Literature"

queryString = """
SELECT DISTINCT ?p ?plbl
WHERE { 

?s ?p wd:Q37922 .
    
?p <http://schema.org/name> ?plbl .

} 
ORDER BY ?plbl
"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P166'), ('plbl', 'award received')]
[('p', 'http://www.wikidata.org/prop/direct/P971'), ('plbl', 'category combines topics')]
[('p', 'http://www.wikidata.org/prop/direct/P301'), ('plbl', "category's main topic")]
[('p', 'http://www.wikidata.org/prop/direct/P527'), ('plbl', 'has part')]
[('p', 'http://www.wikidata.org/prop/direct/P31'), ('plbl', 'instance of')]
[('p', 'http://www.wikidata.org/prop/direct/P360'), ('plbl', 'is a list of')]
[('p', 'http://www.wikidata.org/prop/direct/P921'), ('plbl', 'main subject')]
[('p', 'http://www.wikidata.org/prop/direct/P1411'), ('plbl', 'nominated for')]
[('p', 'http://www.wikidata.org/prop/direct/P179'), ('plbl', 'part of the series')]
[('p', 'http://www.wikidata.org/prop/direct/P793'), ('plbl', 'significant event')]


10

In [48]:
# get predicates from "Nobel Prize in Literature"

queryString = """
SELECT DISTINCT ?p ?plbl
WHERE { 

wd:Q37922 ?p ?o .
    
?p <http://schema.org/name> ?plbl .

} 
ORDER BY ?plbl
"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P2581'), ('plbl', 'BabelNet ID')]
[('p', 'http://www.wikidata.org/prop/direct/P373'), ('plbl', 'Commons category')]
[('p', 'http://www.wikidata.org/prop/direct/P3569'), ('plbl', 'Cultureel Woordenboek ID')]
[('p', 'http://www.wikidata.org/prop/direct/P3509'), ('plbl', 'Dagens Nyheter topic ID')]
[('p', 'http://www.wikidata.org/prop/direct/P9545'), ('plbl', 'Encyclopedia of China Online Database ID')]
[('p', 'http://www.wikidata.org/prop/direct/P1417'), ('plbl', 'Encyclopædia Britannica Online ID')]
[('p', 'http://www.wikidata.org/prop/direct/P646'), ('plbl', 'Freebase ID')]
[('p', 'http://www.wikidata.org/prop/direct/P227'), ('plbl', 'GND ID')]
[('p', 'http://www.wikidata.org/prop/direct/P1296'), ('plbl', 'Gran Enciclopèdia Catalana ID')]
[('p', 'http://www.wikidata.org/prop/direct/P9466'), ('plbl', 'Gyldendals Teaterleksikon ID')]
[('p', 'http://www.wikidata.org/prop/direct/P8408'), ('plbl', 'KBpedia ID')]
[('p', 'http://www.wikidata

33

In [50]:
# get node which is an instance of "Nobel Prize in Literature"

queryString = """
SELECT DISTINCT ?s ?slbl
WHERE { 

?s wdt:P31 wd:Q37922 .
    
?s <http://schema.org/name> ?slbl .

} 
ORDER BY ?slbl
"""

print("Results")
run_query(queryString)

Results
Empty


0

In [52]:
# get node of which "Nobel Prize in Literature" is an instance

queryString = """
SELECT DISTINCT ?o ?olbl
WHERE { 

wd:Q37922 wdt:P31 ?o .
    
?o <http://schema.org/name> ?olbl .

} 
ORDER BY ?olbl
"""

print("Results")
run_query(queryString)

Results
[('o', 'http://www.wikidata.org/entity/Q378427'), ('olbl', 'literary award')]


1

In [2]:
# get winners of "Nobel Prize in literature"

queryString = """
SELECT DISTINCT ?auth ?authlbl
WHERE { 

?auth wdt:P166 wd:Q37922 ;
    wdt:P106/wdt:P279* wd:Q36180 .

?auth <http://schema.org/name> ?authlbl .

} 
ORDER BY ?authlbl
"""

print("Results")
run_query(queryString)

Results
[('auth', 'http://www.wikidata.org/entity/Q34474'), ('authlbl', 'Aleksandr Solzhenitsyn')]
[('auth', 'http://www.wikidata.org/entity/Q234819'), ('authlbl', 'Alice Munro')]
[('auth', 'http://www.wikidata.org/entity/Q42443'), ('authlbl', 'Anatole France')]
[('auth', 'http://www.wikidata.org/entity/Q47484'), ('authlbl', 'André Gide')]
[('auth', 'http://www.wikidata.org/entity/Q34670'), ('authlbl', 'Antonio carglass')]
[('auth', 'http://www.wikidata.org/entity/Q33760'), ('authlbl', 'Bertrand Russell')]
[('auth', 'http://www.wikidata.org/entity/Q46405'), ('authlbl', 'Bjørnstjerne Bjørnson')]
[('auth', 'http://www.wikidata.org/entity/Q392'), ('authlbl', 'Bob Dylan')]
[('auth', 'http://www.wikidata.org/entity/Q41223'), ('authlbl', 'Boris Pasternak')]
[('auth', 'http://www.wikidata.org/entity/Q132589'), ('authlbl', 'Camilo José Cela')]
[('auth', 'http://www.wikidata.org/entity/Q226525'), ('authlbl', 'Carl Spitteler')]
[('auth', 'http://www.wikidata.org/entity/Q131549'), ('authlbl', 'Cl

117

In [3]:
# get winners and nominees of "Nobel Prize in literature" (BAD QUERY)

queryString = """
SELECT ?auth ?authlbl ?num_aw ?num_nom
WHERE { 

OPTIONAL {
    SELECT ?auth (COUNT(?aw) AS ?num_aw)
    WHERE {
    
        ?auth wdt:P166 ?aw ;
            wdt:P106/wdt:P279* wd:Q36180 .

        FILTER (?aw = wd:Q37922)
        
    }
    GROUP BY ?auth
}    

    
OPTIONAL {
    SELECT ?auth (COUNT(?nom) AS ?num_nom)
    WHERE {
    
        ?auth wdt:P1411 ?nom ;
            wdt:P106/wdt:P279* wd:Q36180 .
            
        FILTER (?nom = wd:Q37922)
    
    }
    GROUP BY ?auth

}

?auth <http://schema.org/name> ?authlbl .

FILTER (?num_nom > 0 || ?num_aw > 0)

} 
GROUP BY ?auth ?authlbl ?clbl ?birth ?num_nom ?awlbl ?nomlbl
ORDER BY ?authlbl
"""

print("Results")
run_query(queryString)

Results
[('auth', 'http://www.wikidata.org/entity/Q34474'), ('authlbl', 'Aleksandr Solzhenitsyn'), ('num_aw', '8')]
[('auth', 'http://www.wikidata.org/entity/Q234819'), ('authlbl', 'Alice Munro'), ('num_aw', '4')]
[('auth', 'http://www.wikidata.org/entity/Q42443'), ('authlbl', 'Anatole France'), ('num_aw', '10'), ('num_nom', '21')]
[('auth', 'http://www.wikidata.org/entity/Q47484'), ('authlbl', 'André Gide'), ('num_aw', '9'), ('num_nom', '19')]
[('auth', 'http://www.wikidata.org/entity/Q34670'), ('authlbl', 'Antonio carglass'), ('num_aw', '10'), ('num_nom', '20')]
[('auth', 'http://www.wikidata.org/entity/Q33760'), ('authlbl', 'Bertrand Russell'), ('num_aw', '18'), ('num_nom', '36')]
[('auth', 'http://www.wikidata.org/entity/Q46405'), ('authlbl', 'Bjørnstjerne Bjørnson'), ('num_aw', '4'), ('num_nom', '8')]
[('auth', 'http://www.wikidata.org/entity/Q392'), ('authlbl', 'Bob Dylan'), ('num_aw', '5')]
[('auth', 'http://www.wikidata.org/entity/Q41223'), ('authlbl', 'Boris Pasternak'), ('num

117

In [85]:
# get awards of "Aleksandr Solzhenitsyn"

queryString = """
SELECT ?aw ?awlbl
WHERE {

    wd:Q34474 wdt:P166 ?aw .

    ?aw <http://schema.org/name> ?awlbl .

}
GROUP BY ?awlbl

"""

print("Results")
run_query(queryString)

Results
[('aw', 'http://www.wikidata.org/entity/Q101566864'), ('awlbl', 'honorary doctor of the Syracuse University')]
[('aw', 'http://www.wikidata.org/entity/Q695106'), ('awlbl', 'Order of the Red Star')]
[('aw', 'http://www.wikidata.org/entity/Q37922'), ('awlbl', 'Nobel Prize in Literature')]
[('aw', 'http://www.wikidata.org/entity/Q1026769'), ('awlbl', 'Order of St. Andrew')]
[('aw', 'http://www.wikidata.org/entity/Q278798'), ('awlbl', 'Medal "For the Victory over Germany in the Great Patriotic War 1941–1945"')]
[('aw', 'http://www.wikidata.org/entity/Q1340199'), ('awlbl', 'Lomonosov Gold Medal')]
[('aw', 'http://www.wikidata.org/entity/Q1081503'), ('awlbl', 'Medal "For the Capture of Königsberg"')]
[('aw', 'http://www.wikidata.org/entity/Q603631'), ('awlbl', 'Templeton Prize')]
[('aw', 'http://www.wikidata.org/entity/Q18200478'), ('awlbl', 'Order of the Patriotic War 2nd class')]
[('aw', 'http://www.wikidata.org/entity/Q950604'), ('awlbl', 'Order of the Star of Romania')]


10

In [86]:
# get awards of "Aleksandr Solzhenitsyn"

queryString = """
SELECT ?aw ?awlbl
WHERE {

    wd:Q34474 wdt:P166 ?aw .
    
    FILTER (?aw = wd:Q37922)
    
    ?aw <http://schema.org/name> ?awlbl .

}
GROUP BY ?awlbl

"""

print("Results")
run_query(queryString)

Results
[('aw', 'http://www.wikidata.org/entity/Q37922'), ('awlbl', 'Nobel Prize in Literature')]


1

In [105]:
# GOAL (1)
# get winners and nominees of "Nobel Prize in literature"

queryString = """
SELECT ?auth ?authlbl ?birth (GROUP_CONCAT(?clbl; separator="|") AS ?citizenship) ?num_aw ?num_nom
WHERE { 

OPTIONAL {
    SELECT ?auth ?clbl ?birth (COUNT(?aw) AS ?num_aw)
    WHERE {
    
        ?auth wdt:P166 ?aw ;
            wdt:P27 ?cit ;
            wdt:P569 ?birth .

        FILTER (?aw = wd:Q37922)
        
        ?cit <http://schema.org/name> ?clbl
    }
    GROUP BY ?auth ?clbl ?birth
}    

    
OPTIONAL {
    SELECT ?auth ?clbl ?birth (COUNT(?nom) AS ?num_nom)
    WHERE {
    
        ?auth wdt:P1411 ?nom ;
            wdt:P27 ?cit ;
            wdt:P569 ?birth .
            
        FILTER (?nom = wd:Q37922)
        
        ?cit <http://schema.org/name> ?clbl
    }
    GROUP BY ?auth ?clbl ?birth

}


?auth <http://schema.org/name> ?authlbl .


FILTER (?num_nom > 0 || ?num_aw > 0)

} 
GROUP BY ?auth ?authlbl ?birth ?num_aw ?num_nom
ORDER BY ?authlbl
"""

print("Results")
run_query(queryString)

Results
[('auth', 'http://www.wikidata.org/entity/Q34474'), ('authlbl', 'Aleksandr Solzhenitsyn'), ('birth', '1918-12-11T00:00:00Z'), ('citizenship', 'Soviet Union|Russian Socialist Federative Soviet Republic|Russia'), ('num_aw', '1')]
[('auth', 'http://www.wikidata.org/entity/Q234819'), ('authlbl', 'Alice Munro'), ('birth', '1931-07-10T00:00:00Z'), ('citizenship', 'Canada'), ('num_aw', '1')]
[('auth', 'http://www.wikidata.org/entity/Q42443'), ('authlbl', 'Anatole France'), ('birth', '1844-04-16T00:00:00Z'), ('citizenship', 'France'), ('num_aw', '1'), ('num_nom', '1')]
[('auth', 'http://www.wikidata.org/entity/Q47484'), ('authlbl', 'André Gide'), ('birth', '1869-11-22T00:00:00Z'), ('citizenship', 'France'), ('num_aw', '1'), ('num_nom', '1')]
[('auth', 'http://www.wikidata.org/entity/Q34670'), ('authlbl', 'Antonio carglass'), ('birth', '1913-11-07T00:00:00Z'), ('citizenship', 'France'), ('num_aw', '1'), ('num_nom', '1')]
[('auth', 'http://www.wikidata.org/entity/Q33760'), ('authlbl', 'B

120

In [109]:
# get predicates from "Aleksandr Solzhenitsyn"->"award received"

queryString = """
SELECT ?p ?plbl
WHERE {

    wd:Q34474 wdt:P166 ?aw .
    
    ?aw ?p ?o .    

    ?p <http://schema.org/name> ?plbl .

}
ORDER BY ?plbl

"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P2581'), ('plbl', 'BabelNet ID')]
[('p', 'http://www.wikidata.org/prop/direct/P2581'), ('plbl', 'BabelNet ID')]
[('p', 'http://www.wikidata.org/prop/direct/P2581'), ('plbl', 'BabelNet ID')]
[('p', 'http://www.wikidata.org/prop/direct/P2581'), ('plbl', 'BabelNet ID')]
[('p', 'http://www.wikidata.org/prop/direct/P373'), ('plbl', 'Commons category')]
[('p', 'http://www.wikidata.org/prop/direct/P373'), ('plbl', 'Commons category')]
[('p', 'http://www.wikidata.org/prop/direct/P373'), ('plbl', 'Commons category')]
[('p', 'http://www.wikidata.org/prop/direct/P373'), ('plbl', 'Commons category')]
[('p', 'http://www.wikidata.org/prop/direct/P373'), ('plbl', 'Commons category')]
[('p', 'http://www.wikidata.org/prop/direct/P373'), ('plbl', 'Commons category')]
[('p', 'http://www.wikidata.org/prop/direct/P3569'), ('plbl', 'Cultureel Woordenboek ID')]
[('p', 'http://www.wikidata.org/prop/direct/P3509'), ('plbl', 'Dagens Nyheter topic ID')]
[('p', 

170

In [110]:
# get "inception" values from "Aleksandr Solzhenitsyn"->"award received"

queryString = """
SELECT ?aw ?awlbl ?o
WHERE {

    wd:Q34474 wdt:P166 ?aw .
    
    ?aw wdt:P571 ?o .    

    ?aw <http://schema.org/name> ?awlbl .

}
ORDER BY ?o

"""

print("Results")
run_query(queryString)

Results
[('aw', 'http://www.wikidata.org/entity/Q950604'), ('awlbl', 'Order of the Star of Romania'), ('o', '1864-01-01T00:00:00Z')]
[('aw', 'http://www.wikidata.org/entity/Q37922'), ('awlbl', 'Nobel Prize in Literature'), ('o', '1901-01-01T00:00:00Z')]
[('aw', 'http://www.wikidata.org/entity/Q695106'), ('awlbl', 'Order of the Red Star'), ('o', '1930-04-06T00:00:00Z')]
[('aw', 'http://www.wikidata.org/entity/Q278798'), ('awlbl', 'Medal "For the Victory over Germany in the Great Patriotic War 1941–1945"'), ('o', '1945-05-09T00:00:00Z')]
[('aw', 'http://www.wikidata.org/entity/Q1081503'), ('awlbl', 'Medal "For the Capture of Königsberg"'), ('o', '1945-06-09T00:00:00Z')]
[('aw', 'http://www.wikidata.org/entity/Q603631'), ('awlbl', 'Templeton Prize'), ('o', '1972-01-01T00:00:00Z')]
[('aw', 'http://www.wikidata.org/entity/Q1026769'), ('awlbl', 'Order of St. Andrew'), ('o', '1998-07-01T00:00:00Z')]


7

In [112]:
# get properties from "award received"

queryString = """
SELECT ?p2 ?p2lbl
WHERE {

    wd:Q34474 ?p ?aw .   

    ?p ?p2 ?o .
    
    FILTER (?p = wdt:P166)
    ?p2 <http://schema.org/name> ?p2lbl .

}

"""

print("Results")
run_query(queryString)

Results
Empty


0

In [113]:
# get "winners" from awards

queryString = """
SELECT ?aw ?awlbl ?o ?olbl
WHERE {

    wd:Q34474 wdt:P166 ?aw .
    
    ?aw wdt:P1346 ?o .    

    ?aw <http://schema.org/name> ?awlbl .
    ?o <http://schema.org/name> ?olbl .

}
ORDER BY ?o

"""

print("Results")
run_query(queryString)

Results
[('aw', 'http://www.wikidata.org/entity/Q37922'), ('awlbl', 'Nobel Prize in Literature'), ('o', 'http://www.wikidata.org/entity/Q121180'), ('olbl', 'Władysław Reymont')]
[('aw', 'http://www.wikidata.org/entity/Q37922'), ('awlbl', 'Nobel Prize in Literature'), ('o', 'http://www.wikidata.org/entity/Q131487'), ('olbl', 'Karl Adolph Gjellerup')]
[('aw', 'http://www.wikidata.org/entity/Q37922'), ('awlbl', 'Nobel Prize in Literature'), ('o', 'http://www.wikidata.org/entity/Q159552'), ('olbl', 'Johannes V. Jensen')]
[('aw', 'http://www.wikidata.org/entity/Q37922'), ('awlbl', 'Nobel Prize in Literature'), ('o', 'http://www.wikidata.org/entity/Q18143'), ('olbl', 'Gao Xingjian')]
[('aw', 'http://www.wikidata.org/entity/Q37922'), ('awlbl', 'Nobel Prize in Literature'), ('o', 'http://www.wikidata.org/entity/Q225554'), ('olbl', 'Henrik Pontoppidan')]
[('aw', 'http://www.wikidata.org/entity/Q37922'), ('awlbl', 'Nobel Prize in Literature'), ('o', 'http://www.wikidata.org/entity/Q254032'), ('o

15

In [114]:
# get predicate between "Italy" and "Sovereign State"

queryString = """
SELECT ?p ?plbl
WHERE {

    wd:Q38 ?p wd:Q3624078 .

    ?p <http://schema.org/name> ?plbl .

}
ORDER BY ?plbl

"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P31'), ('plbl', 'instance of')]


1

In [139]:
# get nodes of some requested sovereign states

queryString = """
SELECT ?country ?clbl
WHERE {

    ?country wdt:P31 wd:Q3624078 .

    ?country <http://schema.org/name> ?clbl .
    
    FILTER (CONTAINS(?clbl, "Italy") || CONTAINS(?clbl, "Iran") || CONTAINS(?clbl, "France") || CONTAINS(?clbl, "Denmark") || CONTAINS(?clbl, "Germany")
        || CONTAINS(?clbl, "Romania") || CONTAINS(?clbl, "China"))
}
ORDER BY ?clbl

"""

print("Results")
run_query(queryString)

Results
[('country', 'http://www.wikidata.org/entity/Q35'), ('clbl', 'Denmark')]
[('country', 'http://www.wikidata.org/entity/Q142'), ('clbl', 'France')]
[('country', 'http://www.wikidata.org/entity/Q183'), ('clbl', 'Germany')]
[('country', 'http://www.wikidata.org/entity/Q794'), ('clbl', 'Iran')]
[('country', 'http://www.wikidata.org/entity/Q38'), ('clbl', 'Italy')]
[('country', 'http://www.wikidata.org/entity/Q7318'), ('clbl', 'Nazi Germany')]
[('country', 'http://www.wikidata.org/entity/Q148'), ('clbl', "People's Republic of China")]
[('country', 'http://www.wikidata.org/entity/Q107312248'), ('clbl', 'Republic of China')]
[('country', 'http://www.wikidata.org/entity/Q218'), ('clbl', 'Romania')]


9

In [153]:
# GOAL (2)
# get number of winners for France, Italy and Iran and figure out which is the most prized one
# Answer: France
#
# Note: there are properties which define the year of awards' assignments
    
queryString = """
SELECT ?clbl (COUNT(?auth) AS ?num_win)
WHERE {

    ?cit wdt:P31 wd:Q3624078 .

    ?cit <http://schema.org/name> ?clbl .
    
    FILTER (?cit = wd:Q38 || ?cit = wd:Q142 || ?cit = wd:Q794)
    
    OPTIONAL {
        SELECT ?cit ?auth
        WHERE {

            ?auth wdt:P166 wd:Q37922 ;
                wdt:P27 ?cit .

            ?cit <http://schema.org/name> ?clbl .
        }
    }
}
GROUP BY ?clbl
ORDER BY DESC (?num_win)

"""

print("Results")
run_query(queryString)

Results
[('clbl', 'France'), ('num_win', '17')]
[('clbl', 'Italy'), ('num_win', '3')]
[('clbl', 'Iran'), ('num_win', '0')]


3

In [154]:
# GOAL (3)
# get number of winners for France, Italy and Iran and figure out which is the most prized one
#
# Note: there are properties which define the year of awards' assignments
    
queryString = """
SELECT ?clbl (COUNT(?auth) AS ?num_win)
WHERE {

    ?cit wdt:P31 wd:Q3624078 .

    ?cit <http://schema.org/name> ?clbl .
    
    FILTER (?cit = wd:Q38 || ?cit = wd:Q142 || ?cit = wd:Q794 || ?cit = wd:Q35 || ?cit = wd:Q183 || ?cit = wd:Q148 || ?cit = wd:Q218)
    
    OPTIONAL {
        SELECT ?cit ?auth
        WHERE {

            ?auth wdt:P166 wd:Q37922 ;
                wdt:P27 ?cit .

            ?cit <http://schema.org/name> ?clbl .
        }
    }
}
GROUP BY ?clbl
ORDER BY DESC (?num_win)

"""

print("Results")
run_query(queryString)

Results
[('clbl', 'France'), ('num_win', '17')]
[('clbl', 'Germany'), ('num_win', '6')]
[('clbl', 'Denmark'), ('num_win', '4')]
[('clbl', 'Italy'), ('num_win', '3')]
[('clbl', "People's Republic of China"), ('num_win', '2')]
[('clbl', 'Romania'), ('num_win', '1')]
[('clbl', 'Iran'), ('num_win', '0')]


7

In [7]:
# GOAL (4)
# get umber of winners who have a PhD
# Answer: 2

queryString = """
SELECT (COUNT(DISTINCT ?auth) AS ?num_phd)
WHERE { 

?auth wdt:P166 wd:Q37922 ;
    wdt:P184 ?doc_adv .

} 
"""

print("Results")
run_query(queryString)

Results
[('auth', 'http://www.wikidata.org/entity/Q33760'), ('authlbl', 'Bertrand Russell')]
[('auth', 'http://www.wikidata.org/entity/Q47695'), ('authlbl', 'Rudolf Christoph Eucken')]


2

In [9]:
# get predicates from "Vaticane library"

queryString = """
SELECT DISTINCT ?p ?plbl
WHERE { 

wd:Q213678 ?p ?o .

?p <http://schema.org/name> ?plbl

} 
ORDER BY ?plbl
"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P9226'), ('plbl', 'ARAE ID')]
[('p', 'http://www.wikidata.org/prop/direct/P9037'), ('plbl', 'BHCL UUID')]
[('p', 'http://www.wikidata.org/prop/direct/P2581'), ('plbl', 'BabelNet ID')]
[('p', 'http://www.wikidata.org/prop/direct/P950'), ('plbl', 'Biblioteca Nacional de España ID')]
[('p', 'http://www.wikidata.org/prop/direct/P9522'), ('plbl', 'Biblioteca di Santa Sabina ID')]
[('p', 'http://www.wikidata.org/prop/direct/P268'), ('plbl', 'Bibliothèque nationale de France ID')]
[('p', 'http://www.wikidata.org/prop/direct/P1273'), ('plbl', 'CANTIC ID')]
[('p', 'http://www.wikidata.org/prop/direct/P7865'), ('plbl', 'CoBiS author ID')]
[('p', 'http://www.wikidata.org/prop/direct/P3234'), ('plbl', 'Code List for Cultural Heritage Organizations')]
[('p', 'http://www.wikidata.org/prop/direct/P1612'), ('plbl', 'Commons Institution page')]
[('p', 'http://www.wikidata.org/prop/direct/P373'), ('plbl', 'Commons category')]
[('p', 'http://www.wikidat

60

In [10]:
# get predicates to "Vaticane library"

queryString = """
SELECT DISTINCT ?p ?plbl
WHERE { 

?s ?p wd:Q213678 .

?p <http://schema.org/name> ?plbl

} 
ORDER BY ?plbl
"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P1629'), ('plbl', 'Wikidata item of this property')]
[('p', 'http://www.wikidata.org/prop/direct/P1855'), ('plbl', 'Wikidata property example')]
[('p', 'http://www.wikidata.org/prop/direct/P1416'), ('plbl', 'affiliation')]
[('p', 'http://www.wikidata.org/prop/direct/P485'), ('plbl', 'archives at')]
[('p', 'http://www.wikidata.org/prop/direct/P971'), ('plbl', 'category combines topics')]
[('p', 'http://www.wikidata.org/prop/direct/P301'), ('plbl', "category's main topic")]
[('p', 'http://www.wikidata.org/prop/direct/P195'), ('plbl', 'collection')]
[('p', 'http://www.wikidata.org/prop/direct/P108'), ('plbl', 'employer')]
[('p', 'http://www.wikidata.org/prop/direct/P2378'), ('plbl', 'issued by')]
[('p', 'http://www.wikidata.org/prop/direct/P276'), ('plbl', 'location')]
[('p', 'http://www.wikidata.org/prop/direct/P189'), ('plbl', 'location of discovery')]
[('p', 'http://www.wikidata.org/prop/direct/P921'), ('plbl', 'main subject')]
[('p',

18

In [11]:
# get node which is parent one of a node with the following relationship: "achieves at"->"Vaticane library"

queryString = """
SELECT DISTINCT ?node ?nlbl
WHERE { 

?s wdt:P485 wd:Q213678 ;
    wdt:P31 ?node .
    
?node <http://schema.org/name> ?nlbl

} 
ORDER BY ?nlbl
"""

print("Results")
run_query(queryString)

Results
[('node', 'http://www.wikidata.org/entity/Q5'), ('nlbl', 'human')]


1

In [12]:
# get node which is parent one of a node with the following relationship: "location"->"Vaticane library"

queryString = """
SELECT DISTINCT ?node ?nlbl
WHERE { 

?s wdt:P276 wd:Q213678 ;
    wdt:P31 ?node .
    
?node <http://schema.org/name> ?nlbl

} 
ORDER BY ?nlbl
"""

print("Results")
run_query(queryString)

Results
[('node', 'http://www.wikidata.org/entity/Q1754581'), ('nlbl', 'Evangeliary')]
[('node', 'http://www.wikidata.org/entity/Q1114838'), ('nlbl', 'Legendarium')]
[('node', 'http://www.wikidata.org/entity/Q830560'), ('nlbl', 'bestiary')]
[('node', 'http://www.wikidata.org/entity/Q225672'), ('nlbl', 'breviary')]
[('node', 'http://www.wikidata.org/entity/Q213924'), ('nlbl', 'codex')]
[('node', 'http://www.wikidata.org/entity/Q22948347'), ('nlbl', 'early Quranic manuscript')]
[('node', 'http://www.wikidata.org/entity/Q5292'), ('nlbl', 'encyclopedia')]
[('node', 'http://www.wikidata.org/entity/Q3052382'), ('nlbl', 'fonds')]
[('node', 'http://www.wikidata.org/entity/Q22669139'), ('nlbl', 'fresco')]
[('node', 'http://www.wikidata.org/entity/Q48498'), ('nlbl', 'illuminated manuscript')]
[('node', 'http://www.wikidata.org/entity/Q7725634'), ('nlbl', 'literary work')]
[('node', 'http://www.wikidata.org/entity/Q87167'), ('nlbl', 'manuscript')]
[('node', 'http://www.wikidata.org/entity/Q833590

14

In [13]:
# get predicates of books located in Vatican Library

queryString = """
SELECT DISTINCT ?p ?plbl
WHERE { 

?s wdt:P276 wd:Q213678 ;
    ?p ?o .
    
?p <http://schema.org/name> ?plbl

} 
ORDER BY ?plbl
"""

print("Results")
run_query(queryString)

Results
[('p', 'http://www.wikidata.org/prop/direct/P268'), ('plbl', 'Bibliothèque nationale de France ID')]
[('p', 'http://www.wikidata.org/prop/direct/P373'), ('plbl', 'Commons category')]
[('p', 'http://www.wikidata.org/prop/direct/P935'), ('plbl', 'Commons gallery')]
[('p', 'http://www.wikidata.org/prop/direct/P1417'), ('plbl', 'Encyclopædia Britannica Online ID')]
[('p', 'http://www.wikidata.org/prop/direct/P3462'), ('plbl', 'FAMA work ID')]
[('p', 'http://www.wikidata.org/prop/direct/P646'), ('plbl', 'Freebase ID')]
[('p', 'http://www.wikidata.org/prop/direct/P227'), ('plbl', 'GND ID')]
[('p', 'http://www.wikidata.org/prop/direct/P2671'), ('plbl', 'Google Knowledge Graph ID')]
[('p', 'http://www.wikidata.org/prop/direct/P1296'), ('plbl', 'Gran Enciclopèdia Catalana ID')]
[('p', 'http://www.wikidata.org/prop/direct/P8406'), ('plbl', 'Grove Art Online ID')]
[('p', 'http://www.wikidata.org/prop/direct/P269'), ('plbl', 'IdRef ID')]
[('p', 'http://www.wikidata.org/prop/direct/P244'), 

58

In [15]:
# get authors and their books which are located in Vatican Library

queryString = """
SELECT ?auth ?albl ?book ?blbl
WHERE { 

?book wdt:P276 wd:Q213678 ;
    wdt:P50 ?auth .
    
?auth wdt:P166 wd:Q37922 .
    
?book <http://schema.org/name> ?blbl .
?auth <http://schema.org/name> ?albl .

} 
ORDER BY ?albl
"""

print("Results")
run_query(queryString)

Results
Empty


0

In [18]:
# get authors, their books and the location of the latters

queryString = """
SELECT ?auth ?albl ?book ?blbl ?loc ?llbl
WHERE { 

?book wdt:P276 ?loc ;
    wdt:P50 ?auth .
    
?auth wdt:P166 wd:Q37922 .
    
?book <http://schema.org/name> ?blbl .
?auth <http://schema.org/name> ?albl .
?loc <http://schema.org/name> ?llbl .

} 
ORDER BY ?albl
LIMIT 10
"""

print("Results")
run_query(queryString)

Results
[('auth', 'http://www.wikidata.org/entity/Q42443'), ('albl', 'Anatole France'), ('book', 'http://www.wikidata.org/entity/Q101437270'), ('blbl', 'Les dieux ont soif'), ('loc', 'http://www.wikidata.org/entity/Q100402866'), ('llbl', 'Biblioteca del polo umanistico "E. R. Caianiello"')]
[('auth', 'http://www.wikidata.org/entity/Q42443'), ('albl', 'Anatole France'), ('book', 'http://www.wikidata.org/entity/Q102132052'), ('blbl', 'Monsieur Bergeret a Paris'), ('loc', 'http://www.wikidata.org/entity/Q100402866'), ('llbl', 'Biblioteca del polo umanistico "E. R. Caianiello"')]
[('auth', 'http://www.wikidata.org/entity/Q42443'), ('albl', 'Anatole France'), ('book', 'http://www.wikidata.org/entity/Q101528691'), ('blbl', "L'île des pingouins"), ('loc', 'http://www.wikidata.org/entity/Q100402866'), ('llbl', 'Biblioteca del polo umanistico "E. R. Caianiello"')]
[('auth', 'http://www.wikidata.org/entity/Q42443'), ('albl', 'Anatole France'), ('book', 'http://www.wikidata.org/entity/Q101145738'

10

In [20]:
# GOAL (5)
# get the rank of Literature Nobel award winners who don't have any book at Vatican Library

# Comment of GMS: this returns the authors with their books excluding those in the Vatican library -> NOT CORRECT

queryString = """
SELECT ?auth ?albl (COUNT(?book) AS ?num_books)
WHERE { 

?book wdt:P276 ?loc ;
    wdt:P50 ?auth .
    
?auth wdt:P166 wd:Q37922 .
    
?auth <http://schema.org/name> ?albl .

FILTER (?loc != wd:Q213678)

} 
GROUP BY ?auth ?albl
ORDER BY DESC (?num_books)
LIMIT 10
"""

print("Results")
run_query(queryString)

Results
[('auth', 'http://www.wikidata.org/entity/Q1403'), ('albl', 'Luigi Pirandello'), ('num_books', '40')]
[('auth', 'http://www.wikidata.org/entity/Q41042'), ('albl', 'Harold Pinter'), ('num_books', '33')]
[('auth', 'http://www.wikidata.org/entity/Q37327'), ('albl', 'Samuel Beckett'), ('num_books', '28')]
[('auth', 'http://www.wikidata.org/entity/Q93157'), ('albl', "Eugene O'Neill"), ('num_books', '23')]
[('auth', 'http://www.wikidata.org/entity/Q81685'), ('albl', 'François Mauriac'), ('num_books', '15')]
[('auth', 'http://www.wikidata.org/entity/Q19185'), ('albl', 'George Bernard Shaw'), ('num_books', '12')]
[('auth', 'http://www.wikidata.org/entity/Q42443'), ('albl', 'Anatole France'), ('num_books', '10')]
[('auth', 'http://www.wikidata.org/entity/Q47484'), ('albl', 'André Gide'), ('num_books', '9')]
[('auth', 'http://www.wikidata.org/entity/Q34670'), ('albl', 'Antonio carglass'), ('num_books', '8')]
[('auth', 'http://www.wikidata.org/entity/Q49747'), ('albl', 'Maurice Maeterlinc

10